In [9]:
import json
import csv
import re
import math
import struct

import numpy as np
from matplotlib import pyplot as plt
import matplotlib

import scipy.signal as sig

In [10]:
%matplotlib widget

In [11]:
def read_freq_log(fn):
    with open(fn) as f:
        def parse_freq(f):
            try:
                return float(f)
            except:
                return 0
        freqs = np.trim_zeros(np.array([ parse_freq(line.split()[1]) for line in f.readlines() if re.match('\d+: .*', line) ]))
        return freqs[np.nonzero(freqs)]

In [12]:
fig, axs = plt.subplots(2, 2, figsize=(15, 9))
ax1, ax2, ax3, ax4 = axs.flatten()

freqs_mod, freqs_clean, freqs_clean_gnd = read_freq_log('/mnt/c/Users/jaseg/shared/dsss_test.log'), read_freq_log('/mnt/c/Users/jaseg/shared/dsss_test_50hz_clean.log'), read_freq_log('/mnt/c/Users/jaseg/shared/dsss_test_50hz_clean_gndtest.log')

ax1.plot(freqs_mod)
ax1.grid()

ax2.plot(freqs_clean)
ax2.grid()

ax4.plot(freqs_clean_gnd)
ax4.grid()

w = 512

ax3.psd(freqs_mod[:80000], w, 100/128 * 10)
ax3.psd(freqs_clean[:80000], w, 100/128 * 10)
ax3.psd(freqs_clean_gnd[:80000], w, 100/128 * 10)
None

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [13]:
fig, axs = plt.subplots(2, 2, figsize=(15, 9))
ax1, ax2, ax3, ax4 = axs.flatten()

freqs_mod, freqs_clean = read_freq_log('data/meas_sig_audio_test.log'), read_freq_log('/mnt/c/Users/jaseg/shared/dsss_test_50hz_clean_improved.log')

ax1.plot(freqs_mod)
ax1.grid()

ax2.plot(freqs_clean)
ax2.grid()

w = 512

ax3.psd(freqs_mod[:80000], w, 100/128 * 10)
ax4.psd(freqs_clean[:80000], w, 100/128 * 10)
None

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [44]:
with open('data/dsss_test_demod_fixed_05.bin', 'wb') as f:
    for freq in read_freq_log('data/dsss_test_demod_fixed_05.log'):
        f.write(struct.pack('f', freq))

In [29]:
fig, ax = plt.subplots()
ax.plot(read_freq_log('data/dsss_test_demod_fixed_03.log'))

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [14]:
fig, axs = plt.subplots(2, 1, figsize=(15, 6))
ax1, ax2 = axs.flatten()

freqs_mod = read_freq_log('data/meas_sig_audio_test.log')

with open('data/meas_sig_audio_test.bin', 'wb') as f:
    for freq in freqs_mod:
        f.write(struct.pack('f', freq))
        
with open('data/ref_sig_audio_test.bin', 'rb') as f:
    freqs_ref = np.array(list(struct.iter_unpack('f', f.read())))

ax1.plot(freqs_mod)
ax1.set_title('measured')
ax1.grid()
ax2.plot(freqs_ref)
ax2.set_title('reference')
ax2.grid()

ax1.set_xlim([84250+47, 86000+47])
ax2.set_xlim([84250, 86000])

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

(84250, 86000)

In [15]:
def read_raw_log(fn):
    with open(fn) as f:
        vals = np.array([ int(x, 16) for line in f for x in line.partition(':')[2].split() ])
        return vals

In [19]:
# We see artifacts of the 128sp processing window in the analog readings if we process a buffer immediately after capture. We can reduce these artifacts by deferring the sampling a few milliseconds into the capture period.
# The reason for this is presumably a suboptimal power layout on the cheap f407 devboard leading to CPU load changes dumping noise into our ADC supply.
# In time domain plots we can see frequent high spikes in ADC counts that would be in accordance with this conjecture.

fig, axs = plt.subplots(2, 2, figsize=(15, 9), sharey='row', gridspec_kw={'hspace': 0.2, 'wspace': 0.05})
fig.tight_layout()
ax1, ax2, ax3, ax4 = axs.flatten()

raw_left, raw_right = read_raw_log('data/rawlog_silence_clean.log'), read_raw_log('data/rawlog_silence_clean3.log')
raw_left = raw_left[26000:-10000].astype(float)

raw_right = raw_right[26000:]
raw_right = raw_right[:len(raw_left)].astype(float)

raw_left -= np.mean(raw_left)
raw_right -= np.mean(raw_right)

ax1.set_title('Immediate processing')
ax1.plot(raw_left)
ax1.grid()
for x in range(0, len(raw_left), 128):
    ax1.axvline(x, color='red', alpha=0.3)

ax2.set_title('Deferred processing')
ax2.plot(raw_right)
ax2.grid()
for x in range(0, len(raw_right), 128):
    ax2.axvline(x, color='red', alpha=0.3)

ax1.set_xlim([0, 1000])
ax1.set_ylim([-200, 200])
ax2.set_xlim([0, 1000])
ax2.set_ylim([-200, 200])
ax1.set_xlabel('t [ms]')
ax2.set_xlabel('t [ms]')
ax1.set_ylabel('ADC reading [counts]')

w = 2048

ax3.psd(raw_left, w, 1e3)
ax4.psd(raw_right, w, 1e3)
ax3.set_ylim([-10, 26])
ax4.set_ylim([-10, 26])
ax4.set_ylabel(None)
None

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

<ipython-input-19-55f36f700399>:6: UserWarning: This figure includes Axes that are not compatible with tight_layout, so results might be incorrect.
  fig.tight_layout()


In [17]:
fig, ax = plt.subplots(figsize=(12, 6))

raw_silence = read_raw_log('data/rawlog_silence_clean.log')
raw_silence2 = read_raw_log('data/rawlog_silence_clean3.log')

raw_silence = raw_silence.reshape([-1, 128])
le_mean = raw_silence.mean(axis=0)
ax.plot(le_mean - np.mean(le_mean))

raw_silence2 = raw_silence2.reshape([-1, 128])
le_mean2 = raw_silence2.mean(axis=0)
ax.plot(le_mean2 - np.mean(le_mean2))
ax.grid()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [40]:
fig, axs = plt.subplots(4, 1, figsize=(15, 9), sharex=True)
ax1, ax2, ax3, ax4 = axs.flatten()

#with open('data/meas_sig_audio_test_processed.log') as f:
with open('data/meas_sig_audio_test_fixed_03.log') as f:
    lines = f.readlines()
    data = np.array([ [float(x) for x in line.split(': ')[1].split()] for line in lines if not line.startswith('GROUP:') ])
    groups = [ int(line.split(' ')[2]) for line in lines if line.startswith('GROUP:') ]

ax1.plot(data[:,0])
ax1.grid()
ax1.set_xlim([4000, 16000])
ax1.set_ylim([-0.02, 0.1])

ax2.plot(data[:,1:-2:2])
ax2.grid()
ax2.set_ylim([-0.6, 0.6])

ax3.plot(data[:,2:-2:2])
ax3.grid()

ax4.plot(data[:,-2:])
ax4.grid()

for x in groups:
    ax4.axvline(x, color='red', alpha=0.4)

<ipython-input-40-132a47f1202f>:1: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  fig, axs = plt.subplots(4, 1, figsize=(15, 9), sharex=True)


Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [41]:
ax4.axvline(12433)
ax4.axvline(12164)
ax4.axvline(12475)

In [36]:
fig, axs = plt.subplots(4, 1, figsize=(15, 9), sharex=True)
ax1, ax2, ax3, ax4 = axs.flatten()

with open('data/ref_sig_audio_test_processed.log') as f:
    lines = f.readlines()
    data = np.array([ [float(x) for x in line.split(': ')[1].split()] for line in lines if not line.startswith('GROUP:') ])
    groups = [ int(line.split(': ')[1]) for line in lines if line.startswith('GROUP:') ]

ax1.plot(data[:,0])
ax1.grid()
ax1.set_xlim([82000, 95000])
ax1.set_ylim([-0.02, 0.1])

ax2.plot(data[:,1:-2:2])
ax2.grid()
ax2.set_ylim([-0.6, 0.6])

ax3.plot(data[:,2:-2:2])
ax3.grid()

ax4.plot(data[:,-2:])
ax4.grid()

for x in groups:
    ax4.axvline(x, color='red', alpha=0.4)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [93]:
print(groups)

[516, 518, 4402, 4404, 5537, 7238, 12585, 17497, 17724, 34074, 34076, 41628, 44677, 46287, 49371, 49837, 53877, 54554, 56666, 56949, 60923, 67313, 67744, 67746, 68392, 79601, 84707, 84709, 84711, 85017, 85019, 85021, 85327, 85329, 85637, 85947, 85949, 85951, 86257, 86259, 86261, 86567, 86569, 86571, 86877, 86879, 86881, 87187, 87189, 87191, 87498, 87500, 87807, 87809, 87811, 88117, 88119, 88121, 88427, 88429, 88431, 88488, 88737, 88739, 88741, 89047, 89049, 89051, 89357, 89359, 89361, 89668, 89670, 89730, 89978, 89980, 90287, 90289, 90291, 90598, 90600, 90602, 90907, 90909, 90911, 91217, 91219, 91221, 91527, 91529, 91531, 91837, 91839, 91841, 92148, 92150, 92458, 92460, 92768, 92770, 93078, 93080, 93388, 93390, 93392, 93698, 93700, 93702, 94008, 94010, 94318, 94320]


In [79]:
fig, ax = plt.subplots(figsize=(9, 5))

raw_c = read_raw_log('/mnt/c/Users/jaseg/shared/rawlog_test_c.log')

ax.plot(raw_c[1000:2000])
ax.grid()

<ipython-input-79-e66d1dcc2be5>:1: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  fig, ax = plt.subplots(figsize=(9, 5))


Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [25]:
fig, ax = plt.subplots()
ax.plot([797, 813, 869, 971, 1128, 1298, 1461, 1609, 1750, 1826, 1881, 1860, 1789, 1695, 1552, 1360, 1209, 1048, 921, 832, 803, 812, 870, 972, 1125, 1284, 1461, 1618, 1757, 1834, 1835, 1861, 1795, 1685, 1545, 1383, 1217, 1046, 908, 832,
  800, 815, 864, 993, 1084, 1296, 1453, 1613, 1746, 1833, 1875, 1859, 1794, 1693, 1542, 1352, 1211, 1049, 916, 833, 800, 810, 875, 992, 1144, 1300, 1447, 1606, 1735, 1836, 1846, 1869, 1811, 1701, 1557, 1375, 1208, 1060, 936, 836, 805,
  796, 877, 986, 1134, 1288, 1458, 1613, 1737, 1847, 1865, 1867, 1792, 1688, 1556, 1373, 1209, 1049, 928, 827, 792, 821, 869, 972, 1122, 1295, 1457, 1595, 1745, 1847, 1877, 1867, 1789, 1683, 1539, 1378, 1210, 1047, 917, 833, 817, 821,
  869, 977, 1128, 1299, 1458, 1630, 1711, 1833, 1833, 1869, 1800, 1715, 1545, 1375, 1217, 1060, 917, 841, 812, 826, 878, 985, 1128, 1280, 1452, 1612, 1739, 1827, 1892, 1864, 1793, 1700, 1547, 1375, 1212, 1054, 921, 829, 795, 809, 869,
  990, 1077, 1284, 1459, 1616, 1753, 1864, 1874, 1865, 1807, 1696, 1543, 1390, 1274, 1047, 926, 831, 804, 806, 872, 987, 1100, 1278, 1447, 1604, 1743, 1831, 1879, 1849, 1780, 1660, 1540, 1389, 1176, 1064, 928, 828, 812, 809, 875, 983,
  1128, 1285, 1456, 1611, 1739, 1889, 1879, 1879, 1793, 1680, 1546, 1381, 1215, 1074, 926, 842, 794, 857, 859, 978, 1123, 1290, 1427, 1607, 1737, 1835, 1882, 1861, 1815, 1694, 1532, 1375, 1202, 1050, 928, 822, 802, 810, 854, 990, 1119,
  1292, 1455, 1619, 1738, 1827, 1871, 1847, 1800, 1693, 1551, 1379])

<ipython-input-25-f95a3be8874f>:1: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  fig, ax = plt.subplots()


Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [3]:
fig, ax = plt.subplots()
a = np.array([-00.000732, -00.000352, -00.000666, -00.000202, -00.000706, -00.000006, -00.000597, -00.002039, 000.050663, -00.644566, 004.456614, -16.817095, 034.654587, -39.021217, 024.007816, -08.070650, 001.478795, -00.150260, 000.006110, -00.002328, -00.002322, -00.002426, -00.002177, -00.002452, -00.002333, -00.002438, -00.002342, -00.002396, -00.001979, -00.003049, -00.001720, -00.002686, -00.002168, -00.002507, -00.001868, -00.002899, -00.002017, -00.001952, -00.003255, -00.001080, -00.003335, -00.001575, -00.002704, -00.001872, -00.002735, -00.001983, -00.002191, -00.002478, -00.002155, -00.002203, -00.002328, -00.002206, -00.002443, -00.001770, -00.002718, -00.002004, -00.002378, -00.002112, -00.002122, -00.002691, -00.001679, -00.002690, -00.001946, -00.002232])
b = np.array([-00.002734, -00.001325, -00.002220, -00.003693, -00.004907, -00.006454, -00.007737, 000.004823, -00.363143, 004.688968, -33.795303, 130.992630, -274.092651, 309.377991, -188.427826, 061.912941, -10.974002, 001.053608, -00.048927, 000.007710, 000.007010, 000.006493, 000.007234, 000.006725, 000.006938, 000.006694, 000.006356, 000.006173, 000.006333, 000.005684, 000.005697, 000.005575, 000.005101, 000.005693, 000.004319, 000.005344, 000.004673, 000.003566, 000.006213, 000.002719, 000.004850, 000.003755, 000.004243, 000.003419, 000.003960, 000.003498, 000.003297, 000.003877, 000.002836, 000.003487, 000.003144, 000.002824, 000.003355, 000.002528, 000.002975, 000.003012, 000.002137, 000.003112, 000.002416, 000.002512, 000.002084, 000.003008, 000.001837, 000.002351])
ax.plot([3.906250*i for i in range(len(a))], np.sqrt(a**2 + b**2))
a2 = ax.twiny()
a2.set_xlim([0, len(a)])

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

(0, 64)

In [10]:
fig, ax = plt.subplots()
d = [50.000839,50.000839,50.000832,50.000824,50.000839,50.000832,50.000839,50.000824,50.000847,50.000824,50.000824,50.000839,50.000832,50.000839,50.000824,50.000824,50.000839,50.000824,50.000824,50.000835,50.000816,50.000832,50.000847,50.000832,50.000835,50.000824,50.000824,50.000832,50.000832,50.000843,50.000824,50.000832,50.000832,50.000832,50.000828,50.000832,50.000832,50.000824,50.000816,50.000835,50.000843,50.000824,50.000824,50.000832,50.000832,50.000847,50.000824,50.000824,50.000824,50.000835,50.000835,50.000851,50.000824,50.000824,50.000832,50.000828,50.000828,50.000824,50.000832,50.000835,50.000835,50.000832,50.000847,50.000824,50.000832,50.000839,50.000839,50.000824,50.000832,50.000832,50.000832,50.000835,50.000816,50.000820,50.000824,50.000832,50.000824,50.000832,50.000835,50.000832,50.000816,50.000820,50.000839,50.000839,50.000824,50.000839,50.000820,50.000820,50.000839,50.000832,50.000835,50.000828,50.000824,50.000839,50.000839,50.000839,50.000816,50.000832,50.000824,50.000832,50.000832,50.000839,50.000824,50.000832,50.000828,50.000832,50.000828,50.000835,50.000832,50.000843,50.000839,50.000820,50.000832,50.000835,50.000824,50.000824,50.000828,50.000820,50.000820,50.000828,50.000832,50.000832,50.000828,50.000835,50.000839,50.000820,50.000832,50.000832,50.000824,50.000832,50.000832,50.000839,50.000839,50.000816,50.000828,50.000832,50.000839,50.000824,50.000824,50.000824,50.000835,50.000824,50.000832,50.000839,50.000835,50.000832,50.000828,50.000835,50.000828,50.000828,50.000824,50.000824,50.000839,50.000832,50.000824,50.000832,50.000832,50.000820,50.000851,50.000824,50.000824,50.000839,50.000824,50.000839,50.000832,50.000835,50.000820,50.000832,50.000839,50.000832,50.000832,50.000824,50.000832,50.000824,50.000832,50.000839,50.000839,50.000832,50.000816,50.000835,50.000854,50.000824,50.000816,50.000832,50.000832,50.000835,50.000816,50.000832,50.000824,50.000832,50.000832,50.000832,50.000824,50.000832,50.000824,50.000835,50.000832,50.000835,50.000832,50.000832,50.000828,50.000839,50.000824,50.000839,50.000824,50.000824,50.000839,50.000816,50.000839,50.000816,50.000832,50.000839,50.000839,50.000832,50.000824,50.000832,50.000820,50.000824,50.000835,50.000824,50.000835,50.000832,50.000824,50.000824,50.000820,50.000839,50.000816,50.000832,50.000832,50.000832,50.000824,50.000847,50.000824,50.000839]

ax.plot(d)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [26]:
with open('impl_test_out.json') as f:
    impl_measurements = json.load(f)

In [27]:
fig, axs = plt.subplots(len(impl_measurements), figsize=(8, 20), sharex=True)
fig.tight_layout()
axs = axs.flatten()

for (label, data), ax in zip(impl_measurements.items(), axs):
    ax.set_title(label)
    ax.plot(data[1:-1])
    mean = np.mean(data[1:-1])
    rms = np.sqrt(np.mean(np.square(data[1:-1] - mean)))
    ax.text(0.2, 0.2, f'mean={mean:.3}Hz, rms={rms*1e3:.3}mHz', ha='center', va='center', transform=ax.transAxes,
            bbox=dict(boxstyle="square", ec=(0,0,0,0), fc=(1,1,1,0.8)))

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [3]:
sig.butter(8, 20e-3, output='sos', fs=10.0)

array([[ 2.35232554e-18,  4.70465108e-18,  2.35232554e-18,
         1.00000000e+00, -1.97549493e+00,  9.75650918e-01],
       [ 1.00000000e+00,  2.00000000e+00,  1.00000000e+00,
         1.00000000e+00, -1.97916324e+00,  9.79319515e-01],
       [ 1.00000000e+00,  2.00000000e+00,  1.00000000e+00,
         1.00000000e+00, -1.98597735e+00,  9.86134166e-01],
       [ 1.00000000e+00,  2.00000000e+00,  1.00000000e+00,
         1.00000000e+00, -1.99495144e+00,  9.95108965e-01]])

In [6]:
fig, ax = plt.subplots()
ax.plot([0-0.00012937261, 0-0.00022784119 , 0-0.00039295876 , 0-0.00066361829 , 00-0.0010971602 , 00-0.0017754816 ,
    00-0.0028116399 , 00-0.0043560231 , 00-0.0066005666 , 00-0.0097788338 , 000-0.014159188 , 000-0.020027947 ,
    000-0.027659611 , 000-0.037272236 , 000-0.048968014 , 0000-0.06266222 , 0000-0.07800759 , 000-0.094325546 ,
    0000-0.11055938 , 0000-0.12526666 , 0000-0.13666715 , 0000-0.14275811 , 0000-0.14149973 , 00000-0.1310612 ,
    0000-0.11010384 , 000-0.078063987 , 000-0.035389599 , 00000.016317957 , 00000.074297836 , 000000.13478363 ,
    000000.19331697 , 000000.24519242 , 000000.28597909 , 000000.31204596 , 000000.32101141 , 000000.31204596 ,
    000000.28597909 , 000000.24519242 , 000000.19331697 , 000000.13478363 , 00000.074297836 , 00000.016317957 ,
    000-0.035389599 , 000-0.078063987 , 0000-0.11010384 , 00000-0.1310612 , 0000-0.14149973 , 0000-0.14275811 ,
    0000-0.13666715 , 0000-0.12526666 , 0000-0.11055938 , 000-0.094325546 , 0000-0.07800759 , 0000-0.06266222 ,
    000-0.048968014 , 000-0.037272236 , 000-0.027659611 , 000-0.020027947 , 000-0.014159188 , 00-0.0097788338 ,
    00-0.0066005666 , 00-0.0043560231 , 00-0.0028116399 , 00-0.0017754816 , 00-0.0010971602 , 0-0.00066361829 ,
    0-0.00039295876 , 0-0.00022784119 , 0-0.00012937261 ])

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [25]:
data = np.genfromtxt('/tmp/foo.csv', delimiter=',')[1000:]

In [28]:
fig, axs = plt.subplots(2, figsize=(15, 9), sharex=True)
axs = axs.flatten()
axs[0].set_title('corr')
axs[1].set_title('cwt')
#axs[2].set_title('iir')

axs[0].plot(data[:,0], label='corr')
axs[1].plot(data[:,1], label='cwt')
axs[0].plot(data[:,2], label='avg')
axs[1].plot(data[:,2], label='avg')

for ax in axs:
    ax.legend()
    ax.grid()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …